In [1]:
from cobra.io import load_json_model
from cobra.flux_analysis import pfba
from cobra.exceptions import Infeasible
from os import getcwd
import numpy as np
from joblib import Parallel, delayed
from tqdm import tqdm
from pandas import DataFrame
from optlang import Model, Variable, Constraint, Objective

In [2]:
relative_directory = getcwd()
model = load_json_model(relative_directory + '/Reconstructions/MethylococcusModel15.json')

In [3]:
model.reactions.EX_n2_e.bounds = 0, 1000

In [4]:
# Rewrite efficiency_prediction_alt_3 to work with cobrapy, and to use pfba.
# Not accounting for the effect of NO2 production on the system!!!
def efficiency_prediction_alt_3(n_source,lim,ratio):
    o2_utr = []
    ch4_utr = []
    grwth_rate = []
    sol_array = []
    
    for l in range(len(n_source)):
        with model:
            model.reactions.BIOMASS_Mcapsulatus.bounds = 0.1, 0.1
            
            if not ratio[l] == 100:
                model.reactions.SMMOi.bounds = 0, 1000
                model.reactions.CYTCBDipp.bounds = 0, 1000
                model.reactions.PPA3ipp.bounds = 0, 1000
                c1 = model.problem.Constraint(
                    (model.reactions.PMMODCipp.flux_expression + model.reactions.PMMOipp.flux_expression) -
                    (ratio[l]/(100.0-ratio[l]))* model.reactions.SMMOi.flux_expression ,lb=0, ub=0, name='c1',)
                model.add_cons_vars(c1)

            else:
                model.reactions.SMMOi.bounds = 0, 0
                model.reactions.CYTCBDipp.bounds = 0, 0
                model.reactions.PPA3ipp.bounds = 0, 0
                
    #####################################################################################

            if n_source[l] == 'no3':
                model.reactions.EX_nh4_e.bounds = 0, 1000
                model.reactions.EX_no3_e.bounds = -1000, 1000
                model.reactions.GLNS.bounds = 0, 1000

            elif n_source[l] == 'nh4':
                model.reactions.EX_nh4_e.bounds = -1000, 1000
                model.reactions.EX_no3_e.bounds = 0, 1000
                model.reactions.GLNS.bounds = 0, 0
                model.reactions.HAORipp.bounds= 0, 1000
#                 c3 = model.problem.Constraint(
#                     model.reactions.EX_nh4_e.flux_expression - 4* model.reactions.EX_no2_e.flux_expression, lb=0, ub=0, name='c3')
#                 model.add_cons_vars(c3)
                if not ratio[l] == 100:
                    model.reactions.SAMMOi.bounds = 0, 1000
                    c4 = model.problem.Constraint(
                        model.reactions.PAMMOipp.flux_expression -
                    (ratio[l]/(100.0-ratio[l]))* model.reactions.SAMMOi.flux_expression ,lb=0, ub=0, name='c4')
                    model.add_cons_vars(c4)
                else:
                    model.reactions.SAMMOi.bounds = 0, 0

            elif n_source[l] == 'both':
                model.reactions.EX_no3_e.bounds = -1000, 1000
                model.reactions.EX_nh4_e.bounds = -1000, 1000
                model.reactions.GLNS.bounds = 0, 1000
                model.reactions.HAORipp.bounds = 0, 1000
#                 c3 = model.problem.Constraint(
#                     model.reactions.EX_nh4_e.flux_expression + 4* model.reactions.EX_no2_e.flux_expression, lb=0, ub=0, name='c3')
#                 model.add_cons_vars(c3)
                c2 = model.problem.Constraint(
                    model.reactions.EX_nh4_e.flux_expression - 4.12* model.reactions.EX_no3_e.flux_expression, lb=0, ub=0, name='c2')
                model.add_cons_vars(c2)
                if not ratio[l] == 100:
                    model.reactions.SAMMOi.bounds = 0, 1000
                    c4 = model.problem.Constraint(
                        model.reactions.PAMMOipp.flux_expression -
                    (ratio[l]/(100.0-ratio[l]))* model.reactions.SAMMOi.flux_expression ,lb=0, ub=0, name='c4')
                    model.add_cons_vars(c4)
                else:
                    model.reactions.SAMMOi.bounds = 0, 0

    #####################################################################################

            if lim[l] == 'O2':
                model.reactions.EX_o2_e.bounds = -1000, 0
                model.reactions.EX_ch4_e.bounds = -1000, 0
                model.reactions.EX_co2_e.bounds = -1000, 1000

                model.objective = model.reactions.EX_o2_e
                model.objective.direction = 'max'

                try:
                    solved_o2_utr = model.slim_optimize()
                    if np.isnan(solved_o2_utr):
                        raise AssertionError
                    else:
                        o2_utr.append(solved_o2_utr)
                        model.reactions.EX_o2_e.bounds = solved_o2_utr, solved_o2_utr

                    model.objective = model.reactions.EX_ch4_e
                    model.objective.direction = 'max'
                    solution = pfba(model)

                    ch4_utr.append(model.reactions.EX_ch4_e.flux)
                    grwth_rate.append(model.reactions.BIOMASS_Mcapsulatus.flux)
                    sol_array.append(solution.fluxes)

                except (Infeasible, AssertionError) as e:
                    o2_utr.append(0)
                    ch4_utr.append(0)
                    sol_array.append(0)
                    grwth_rate.append(0)


            elif lim[l] == 'CH4':
                model.reactions.EX_o2_e.bounds = -1000, 0
                model.reactions.EX_ch4_e.bounds = -1000, 0
                model.reactions.EX_co2_e.bounds = -1000, 1000

                model.objective = model.reactions.EX_ch4_e
                model.objective.direction = 'max'

                try:
                    solved_ch4_utr = model.slim_optimize()
                    if np.isnan(solved_ch4_utr):
                        raise AssertionError
                    else:
                        ch4_utr.append(solved_ch4_utr)
                        model.reactions.EX_ch4_e.bounds = solved_ch4_utr, solved_ch4_utr                               

                    model.objective = model.reactions.EX_o2_e
                    model.objective.direction = 'max'
                    solution = pfba(model)

                    o2_utr.append(model.reactions.EX_o2_e.flux)
                    grwth_rate.append(model.reactions.BIOMASS_Mcapsulatus.flux)
                    sol_array.append(solution.fluxes)

                    
                except (Infeasible, AssertionError) as e:
                    o2_utr.append(0)
                    sol_array.append(0)
                    ch4_utr.append(0)
                    grwth_rate.append(0)

    ######################################################################################
#            print([(rxn.id,rxn.flux) for rxn in model.reactions if rxn.id.startswith('EX_') and rxn.flux > 0])
        
    return o2_utr, ch4_utr, grwth_rate, sol_array

In [6]:
def mean_absolute_error(o2_utr,ch4_utr,grwth_rate,o2_ch4_yields_exp):
    sum_of_errors = 0
    fitness = 99
    try:
        ratios = [abs(float(o2_utr[i]/ch4_utr[i])) for i in range(len(o2_utr))]
        yields = [grwth_rate[i]/((ch4_utr[i]/1000)*16.04) for i in range(len(o2_utr))]
#         print ratios
    
        for x in range(len(ratios)):
            sum_of_errors = sum_of_errors + abs((ratios[x] - o2_ch4_yields_exp[x]))    
    
        fitness = sum_of_errors/len(ratios)
        #print fitness
        return fitness
    
    except ZeroDivisionError:
        #print fitness
        return fitness

In [7]:
def hard_evaluation_methylococcus_model(tup):
    print tup
    model.reactions.PMMOipp.bounds = tup[0], tup[0]
    model.reactions.PMMODCipp.bounds = tup[1], tup[1]
    model.reactions.CYOR_q8ppi.bounds = tup[2], tup[2]
    
    o2_utr, ch4_utr, grwth_rate, sol_array = efficiency_prediction_alt_3(n_sources,lim,ratio)
    fitness = mean_absolute_error(o2_utr,ch4_utr,grwth_rate,o2_ch4_yields_exp)
    
    return fitness

In [8]:
# Experimental parameters used by Leak and Dalton, 
# here serve as input parameters for the Efficiency Prediction function.

n_sources = ['no3','no3','no3','no3','nh4','nh4','nh4','both','both']
lim = ['O2','O2','CH4','CH4','O2','O2','CH4','CH4','CH4']
ratio = [2,100,1,99,2,99,96,100,2]
cu_values = [0.8,6,0.2,6,0.4,6,6,6.4,0.2]


# Experimental results as measured by Leak and Dalton
o2_ch4_yields_exp = [1.47,1.45,1.50,1.41,1.56,1.60,1.60,1.48,1.52]
ych4_yields_exp = [0.50,0.69,0.50,0.67,0.71,'0.69-0.75',0.67,0.79,0.60]

In [9]:
# Subselection of those where pMMO is (most) active. This is going to be the training set.
# I will also focus on fitting the values to NO3 and Both Nitrogen sources, not to pure
# NH4, to avoid fitting to the 'toxic' effects of NO2.
n_sources = [n_sources[1],n_sources[3],n_sources[5],n_sources[6],n_sources[7]]
lim = [lim[1],lim[3],lim[5],lim[6],lim[7]]
ratio = [ratio[1],ratio[3],ratio[5],ratio[6],ratio[7]]
cu_values = [cu_values[1],cu_values[3],cu_values[5],cu_values[6],cu_values[7]]
o2_ch4_yields_exp = [o2_ch4_yields_exp[1],o2_ch4_yields_exp[3],o2_ch4_yields_exp[5],o2_ch4_yields_exp[6],o2_ch4_yields_exp[7]]
ych4_yields_exp = [ych4_yields_exp[1],ych4_yields_exp[3],ych4_yields_exp[5],ych4_yields_exp[6],ych4_yields_exp[7]]

### First 8th

In [10]:
# Define 1st quadrant of parameter space
xmin, xmax, xstep = 0, 5, 0.1
ymin, ymax, ystep = 0, 5, 0.1
zmin, zmax, zstep = -5, 0, 0.1

In [11]:
# Reshaping lists of matrices into a single vector/list of tuples with all 
# possible combinations of x,y,z as one tuple
tup = np.vstack(np.meshgrid(
    np.arange(xmin, xmax + xstep, xstep), 
    np.arange(ymin, ymax + ystep, ystep),  
    np.arange(zmin, zmax + zstep, zstep))).reshape(3,-1).T

In [12]:
dict_result_combo = {}

In [13]:
fitness = (Parallel(n_jobs=-1,verbose=10)(delayed(hard_evaluation_methylococcus_model)(elem) for elem in tup))

[ 0.  0. -5.]
[ 0.   0.  -4.9]
[ 0.   0.  -4.8]
[ 0.   0.  -4.7]
[ 0.   0.  -4.6]
[ 0.   0.  -4.5]
[ 0.   0.  -4.4]
[ 0.   0.  -4.3]
[ 0.   0.  -4.2]
[ 0.   0.  -4.1]
[ 0.  0. -4.]
[ 0.   0.  -3.9]


[Parallel(n_jobs=-1)]: Done   5 tasks      | elapsed:    0.6s


[ 0.   0.  -3.7]
[ 0.   0.  -3.8]
[ 0.   0.  -3.6]
[ 0.   0.  -3.5]


[Parallel(n_jobs=-1)]: Done  10 tasks      | elapsed:    0.9s


[ 0.   0.  -3.4]
[ 0.   0.  -3.3]
[ 0.   0.  -3.2]
[ 0.   0.  -3.1]
[ 0.  0. -3.]
[ 0.   0.  -2.9]
[ 0.   0.  -2.8]
[ 0.   0.  -2.7]


...

[ 4.   5.  -4.5]
[ 4.   5.  -4.4]
[ 4.   5.  -4.3]
[ 4.   5.  -4.2]
[ 4.   5.  -4.1]
[ 4.  5. -4.]
[ 4.   5.  -3.9]
[ 4.   5.  -3.8]
[ 4.   5.  -3.7]
[ 4.   5.  -3.6]
[ 4.   5.  -3.5]
[ 4.   5.  -3.4]
[ 4.   5.  -3.3]
[ 4.   5.  -3.2]
[ 4.   5.  -3.1]
[ 4.  5. -3.]
[ 4.   5.  -2.9]
[ 4.   5.  -2.8]
[ 4.   5.  -2.7]
[ 4.   5.  -2.6]
[ 4.   5.  -2.5]
[ 4.   5.  -2.4]
[ 4.   5.  -2.3]
[ 4.   5.  -2.2]
[ 4.   5.  -2.1]
[ 4.  5. -2.]
[ 4.   5.  -1.9]
[ 4.   5.  -1.8]
[ 4.   5.  -1.7]
[ 4.   5.  -1.6]
[ 4.   5.  -1.5]
[ 4.   5.  -1.4]
[ 4.   5.  -1.3]
[ 4.   5.  -1.2]
[ 4.   5.  -1.1]
[ 4.  5. -1.]
[ 4.   5.  -0.9]
[ 4.   5.  -0.8]
[ 4.   5.  -0.7]
[ 4.   5.  -0.6]
[ 4.   5.  -0.5]
[ 4.   5.  -0.4]
[ 4.   5.  -0.3]
[ 4.   5.  -0.2]
[ 4.   5.  -0.1]
[ 4.00000000e+00  5.00000000e+00 -1.77635684e-14]
[ 4.1  5.  -5. ]
[ 4.1  5.  -4.9]
[ 4.1  5.  -4.8]
[ 4.1  5.  -4.7]
[ 4.1  5.  -4.6]
[ 4.1  5.  -4.5]
[ 4.1  5.  -4.4]
[ 4.1  5.  -4.3]
[ 4.1  5.  -4.2]
[ 4.1  5.  -4.1]
[ 4.1  5.  -4. ]
[ 4.1  5. 

[ 4.9  5.  -3.8]
[ 4.9  5.  -3.7]
[ 4.9  5.  -3.6]
[ 4.9  5.  -3.5]
[ 4.9  5.  -3.4]
[ 4.9  5.  -3.3]
[ 4.9  5.  -3.2]
[ 4.9  5.  -3.1]
[ 4.9  5.  -3. ]
[ 4.9  5.  -2.9]
[ 4.9  5.  -2.8]
[ 4.9  5.  -2.7]
[ 4.9  5.  -2.6]
[ 4.9  5.  -2.5]
[ 4.9  5.  -2.4]
[ 4.9  5.  -2.3]
[ 4.9  5.  -2.2]
[ 4.9  5.  -2.1]
[ 4.9  5.  -2. ]
[ 4.9  5.  -1.9]
[ 4.9  5.  -1.8]
[ 4.9  5.  -1.7]
[ 4.9  5.  -1.6]
[ 4.9  5.  -1.5]
[ 4.9  5.  -1.4]
[ 4.9  5.  -1.3]
[ 4.9  5.  -1.2]
[ 4.9  5.  -1.1]
[ 4.9  5.  -1. ]
[ 4.9  5.  -0.9]
[ 4.9  5.  -0.8]
[ 4.9  5.  -0.7]
[ 4.9  5.  -0.6]
[ 4.9  5.  -0.5]
[ 4.9  5.  -0.4]
[ 4.9  5.  -0.3]
[ 4.9  5.  -0.2]
[ 4.9  5.  -0.1]
[ 4.90000000e+00  5.00000000e+00 -1.77635684e-14]
[ 5.  5. -5.]
[ 5.   5.  -4.9]
[ 5.   5.  -4.8]
[ 5.   5.  -4.7]
[ 5.   5.  -4.6]
[ 5.   5.  -4.5]
[ 5.   5.  -4.4]
[ 5.   5.  -4.3]
[ 5.   5.  -4.2]
[ 5.   5.  -4.1]


[Parallel(n_jobs=-1)]: Done 132605 tasks      | elapsed: 323.9min


[ 5.  5. -4.]
[ 5.   5.  -3.9]
[ 5.   5.  -3.8]
[ 5.   5.  -3.7]
[ 5.   5.  -3.6]
[ 5.   5.  -3.5]
[ 5.   5.  -3.4]
[ 5.   5.  -3.3]
[ 5.   5.  -3.2]
[ 5.   5.  -3.1]
[ 5.  5. -3.]
[ 5.   5.  -2.9]
[ 5.   5.  -2.8]
[ 5.   5.  -2.7]
[ 5.   5.  -2.6]
[ 5.   5.  -2.5]
[ 5.   5.  -2.4]
[ 5.   5.  -2.3]
[ 5.   5.  -2.2]
[ 5.   5.  -2.1]
[ 5.  5. -2.]
[ 5.   5.  -1.9]
[ 5.   5.  -1.8]
[ 5.   5.  -1.7]
[ 5.   5.  -1.6]
[ 5.   5.  -1.5]
[ 5.   5.  -1.4]
[ 5.   5.  -1.3]
[ 5.   5.  -1.2]
[ 5.   5.  -1.1]
[ 5.  5. -1.]
[ 5.   5.  -0.9]
[ 5.   5.  -0.8]
[ 5.   5.  -0.7]
[ 5.   5.  -0.6]
[ 5.   5.  -0.5]
[ 5.   5.  -0.4]
[ 5.   5.  -0.3]
[ 5.   5.  -0.2]
[ 5.   5.  -0.1]
[ 5.00000000e+00  5.00000000e+00 -1.77635684e-14]


[Parallel(n_jobs=-1)]: Done 132651 out of 132651 | elapsed: 324.2min finished


In [14]:
result_combo = zip(tup,fitness)

In [15]:
for i, line in tqdm(enumerate(result_combo)):
    if i not in dict_result_combo.keys():
        dict_result_combo[i]= {'redox-arm':line[0][0],'direct-coupling':line[0][1],
                           'uphill-electron-transfer':line[0][2],'fitness':line[1]}
    else:
        pass

132651it [05:43, 386.49it/s]


In [16]:
df = DataFrame(dict_result_combo)
df_transposed = df.T
df_transposed.to_csv('/Users/clie/Desktop/EFPro2/Experimental Data & Standards/Parallelized Parameter Fitting/HPC Re-run/Results/FirstEighth.csv')

### Second 8th

In [17]:
# Define 1st quadrant of parameter space
xmin, xmax, xstep = 5, 10, 0.1
ymin, ymax, ystep = 0, 5, 0.1
zmin, zmax, zstep = -5, 0, 0.1

In [18]:
# Reshaping lists of matrices into a single vector/list of tuples with all 
# possible combinations of x,y,z as one tuple
tup = np.vstack(np.meshgrid(
    np.arange(xmin, xmax + xstep, xstep), 
    np.arange(ymin, ymax + ystep, ystep),  
    np.arange(zmin, zmax + zstep, zstep))).reshape(3,-1).T

In [19]:
dict_result_combo = {}

In [20]:
fitness = (Parallel(n_jobs=-1,verbose=10)(delayed(hard_evaluation_methylococcus_model)(elem) for elem in tup))

[ 5.  0. -5.]
[ 5.   0.  -4.7]
[ 5.   0.  -4.9]
[ 5.   0.  -4.8]
[ 5.   0.  -4.6]
[ 5.   0.  -4.5]
[ 5.   0.  -4.4]
[ 5.   0.  -4.3]
[ 5.   0.  -4.2]
[ 5.   0.  -4.1]
[ 5.  0. -4.]
[ 5.   0.  -3.9]


[Parallel(n_jobs=-1)]: Done   5 tasks      | elapsed:    0.7s


[ 5.   0.  -3.8]
[ 5.   0.  -3.7]
[ 5.   0.  -3.6]
[ 5.   0.  -3.5]


[Parallel(n_jobs=-1)]: Done  10 tasks      | elapsed:    1.0s


[ 5.   0.  -3.4]
[ 5.   0.  -3.3]
[ 5.   0.  -3.2]
[ 5.   0.  -3.1]
[ 5.  0. -3.]
[ 5.   0.  -2.9]
[ 5.   0.  -2.8]
[ 5.   0.  -2.7]


...

[ 9.   5.  -4.6]
[ 9.   5.  -4.5]
[ 9.   5.  -4.4]
[ 9.   5.  -4.3]
[ 9.   5.  -4.2]
[ 9.   5.  -4.1]
[ 9.  5. -4.]
[ 9.   5.  -3.9]
[ 9.   5.  -3.8]
[ 9.   5.  -3.7]
[ 9.   5.  -3.6]
[ 9.   5.  -3.5]
[ 9.   5.  -3.4]
[ 9.   5.  -3.3]
[ 9.   5.  -3.2]
[ 9.   5.  -3.1]
[ 9.  5. -3.]
[ 9.   5.  -2.9]
[ 9.   5.  -2.8]
[ 9.   5.  -2.7]
[ 9.   5.  -2.6]
[ 9.   5.  -2.5]
[ 9.   5.  -2.4]
[ 9.   5.  -2.3]
[ 9.   5.  -2.2]
[ 9.   5.  -2.1]
[ 9.  5. -2.]
[ 9.   5.  -1.9]
[ 9.   5.  -1.8]
[ 9.   5.  -1.7]
[ 9.   5.  -1.6]
[ 9.   5.  -1.5]
[ 9.   5.  -1.4]
[ 9.   5.  -1.3]
[ 9.   5.  -1.2]
[ 9.   5.  -1.1]
[ 9.  5. -1.]
[ 9.   5.  -0.9]
[ 9.   5.  -0.8]
[ 9.   5.  -0.7]
[ 9.   5.  -0.6]
[ 9.   5.  -0.5]
[ 9.   5.  -0.4]
[ 9.   5.  -0.3]
[ 9.   5.  -0.2]
[ 9.   5.  -0.1]
[ 9.00000000e+00  5.00000000e+00 -1.77635684e-14]
[ 9.1  5.  -5. ]
[ 9.1  5.  -4.9]
[ 9.1  5.  -4.8]
[ 9.1  5.  -4.7]
[ 9.1  5.  -4.6]
[ 9.1  5.  -4.5]
[ 9.1  5.  -4.4]
[ 9.1  5.  -4.3]
[ 9.1  5.  -4.2]
[ 9.1  5.  -4.1]
[ 9.1  5. 

[ 9.9  5.  -3.9]
[ 9.9  5.  -3.8]
[ 9.9  5.  -3.7]
[ 9.9  5.  -3.6]
[ 9.9  5.  -3.5]
[ 9.9  5.  -3.4]
[ 9.9  5.  -3.3]
[ 9.9  5.  -3.2]
[ 9.9  5.  -3.1]
[ 9.9  5.  -3. ]
[ 9.9  5.  -2.9]
[ 9.9  5.  -2.8]
[ 9.9  5.  -2.7]
[ 9.9  5.  -2.6]
[ 9.9  5.  -2.5]
[ 9.9  5.  -2.4]
[ 9.9  5.  -2.3]
[ 9.9  5.  -2.2]
[ 9.9  5.  -2.1]
[ 9.9  5.  -2. ]
[ 9.9  5.  -1.9]
[ 9.9  5.  -1.8]
[ 9.9  5.  -1.7]
[ 9.9  5.  -1.6]
[ 9.9  5.  -1.5]
[ 9.9  5.  -1.4]
[ 9.9  5.  -1.3]
[ 9.9  5.  -1.2]
[ 9.9  5.  -1.1]
[ 9.9  5.  -1. ]
[ 9.9  5.  -0.9]
[ 9.9  5.  -0.8]
[ 9.9  5.  -0.7]
[ 9.9  5.  -0.6]
[ 9.9  5.  -0.5]
[ 9.9  5.  -0.4]
[ 9.9  5.  -0.3]
[ 9.9  5.  -0.2]
[ 9.9  5.  -0.1]
[ 9.90000000e+00  5.00000000e+00 -1.77635684e-14]
[10.  5. -5.]
[10.   5.  -4.9]
[10.   5.  -4.8]
[10.   5.  -4.7]
[10.   5.  -4.6]
[10.   5.  -4.5]
[10.   5.  -4.4]
[10.   5.  -4.3]
[10.   5.  -4.2]


[Parallel(n_jobs=-1)]: Done 132605 tasks      | elapsed: 903.2min


[10.   5.  -4.1]
[10.  5. -4.]
[10.   5.  -3.9]
[10.   5.  -3.8]
[10.   5.  -3.7]
[10.   5.  -3.6]
[10.   5.  -3.5]
[10.   5.  -3.4]
[10.   5.  -3.3]
[10.   5.  -3.2]
[10.   5.  -3.1]
[10.  5. -3.]
[10.   5.  -2.9]
[10.   5.  -2.8]
[10.   5.  -2.7]
[10.   5.  -2.6]
[10.   5.  -2.5]
[10.   5.  -2.4]
[10.   5.  -2.3]
[10.   5.  -2.2]
[10.   5.  -2.1]
[10.  5. -2.]
[10.   5.  -1.9]
[10.   5.  -1.8]
[10.   5.  -1.7]
[10.   5.  -1.6]
[10.   5.  -1.5]
[10.   5.  -1.4]
[10.   5.  -1.3]
[10.   5.  -1.2]
[10.   5.  -1.1]
[10.  5. -1.]
[10.   5.  -0.9]
[10.   5.  -0.8]
[10.   5.  -0.7]
[10.   5.  -0.6]
[10.   5.  -0.5]
[10.   5.  -0.4]
[10.   5.  -0.3]
[10.   5.  -0.2]
[10.   5.  -0.1]
[ 1.00000000e+01  5.00000000e+00 -1.77635684e-14]


[Parallel(n_jobs=-1)]: Done 132651 out of 132651 | elapsed: 903.8min finished


In [21]:
result_combo = zip(tup,fitness)

In [22]:
for i, line in tqdm(enumerate(result_combo)):
    if i not in dict_result_combo.keys():
        dict_result_combo[i]= {'redox-arm':line[0][0],'direct-coupling':line[0][1],
                           'uphill-electron-transfer':line[0][2],'fitness':line[1]}
    else:
        pass

132651it [08:34, 257.65it/s]


In [23]:
df = DataFrame(dict_result_combo)
df_transposed = df.T
df_transposed.to_csv('/Users/clie/Desktop/EFPro2/Experimental Data & Standards/Parallelized Parameter Fitting/HPC Re-run/Results/SecondEighth.csv')

In [30]:
model.metabolites.n2_c.reactions

frozenset({<Reaction N2trpp at 0x111528810>, <Reaction NIT_mc at 0x111537d90>})

In [32]:
model.reactions.PAMMOipp

<Reaction PAMMOipp at 0x11156fb10>